In [1]:
import pandas as pd
import seaborn as sns
import os
import matplotlib.pyplot as plt

In [2]:
agg_df = pd.DataFrame()

workdir_path = 'wos_downloads/aggregated'
for root, dirs, files in os.walk(workdir_path):
    for filename in files:
        if 'analyze_' in filename:
            path=os.path.join(root, filename)
            with open(os.path.join(root, 'query.txt'),'r') as f:
                query = f.readline()
            chunk = pd.read_csv(path, sep='\t')[["Publication Years","Record Count"]]
            chunk["name"] = filename.replace(".txt","")
            chunk["query"] = query
            agg_df = pd.concat([chunk,agg_df],ignore_index=True)

In [3]:
agg_df["region"] = agg_df["query"].apply(lambda x: "EU+China" if "CU" in x else "Global")
agg_df["kw_token"] = agg_df["query"].apply(lambda x: x.split("TS=(")[-1].split(")")[0])
agg_df["kw_token"] = agg_df["kw_token"].apply(lambda x: "OR COMPOSITE" if " OR " in x else x)

In [4]:
agg_df = agg_df[~agg_df["Record Count"].isna()]

In [5]:
agg_df.groupby("query",as_index=False)["Record Count"].sum()

query  Record Count
0    CU=(PEOPLES R CHINA OR HONG KONG) AND CU=(AUST...         972.0
1    CU=(PEOPLES R CHINA OR HONG KONG) AND CU=(AUST...         451.0
2    CU=(PEOPLES R CHINA OR HONG KONG) AND CU=(AUST...          30.0
3    CU=(PEOPLES R CHINA OR HONG KONG) AND CU=(AUST...          12.0
4    CU=(PEOPLES R CHINA OR HONG KONG) AND CU=(AUST...           5.0
..                                                 ...           ...
384          TS=("word embedding*") AND PY=(2011-2022)        7068.0
385             TS=("word vector*") AND PY=(2011-2022)        1747.0
386  TS=(("face recognition" NOT "brain")) AND PY=(...       19690.0
387  TS=(("object detection" NOT "brain")) AND PY=(...       28989.0
388  TS=(("speech recognition" NOT "brain")) AND PY...       19912.0

[389 rows x 2 columns]

In [6]:
# agg_df = agg_df[agg_df["Publication Years"].str.startswith("20", na=False)].copy()
# agg_df["Publication Years"] = agg_df["Publication Years"].astype(int)
# agg_df[((agg_df["Publication Years"]>2010) & (agg_df["Publication Years"]<2023))]

In [7]:
# agg_df["Publication Years"].value_counts()

In [8]:
agg_df.to_excel(r'C:\Users\radvanyi\PycharmProjects\ZSI_analytics\WOS\wos_processed_data\query_yearly_agg.xlsx', index=False)